In [2]:
import sys
import os
from pathlib import Path

project_root = Path(__file__).parent.parent if '__file__' in globals() else Path.cwd().parent
sys.path.insert(0, str(project_root))

from core.backtesting_opt import _Data, Strategy, Backtest
from utils.functions import BlackScholes as bs
import pandas as pd
import numpy as np
import math
from scipy.optimize import root_scalar
from datetime import datetime, date as DateObject,time


In [16]:
class StraddleSpikeShort(Strategy):
    position_id = "STRADDLE_SPIKE"

    def init(self):
        self.strike_step = 50
        self.expiry_range = [9, 16]
        self.day_straddle_base = None
        self.last_day = None
        self.in_position = False

    def next(self):
        if self.spot is None or pd.isna(self.spot):
            return

        now = self.time.date()
        current_time = self.time.time()
        # Reset for new day
        if self.last_day != now:
            self.last_day = now
            self.day_straddle_base = None
            self.in_position = False

        # Strike logic
        atm = round(self.spot / self.strike_step) * self.strike_step
        valid_ttes = [tte for tte in self.tte_to_expiry if self.expiry_range[0] <= tte <= self.expiry_range[1]]
        if not valid_ttes:
            return

        tte = min(valid_ttes)
        expiry = self.tte_to_expiry[tte]

        leg_ce = f"NIFTY{pd.Timestamp(expiry).strftime('%d%b%y').upper()}{atm}CE"
        leg_pe = f"NIFTY{pd.Timestamp(expiry).strftime('%d%b%y').upper()}{atm}PE"

        ce_data = self._data.get_ticker_data(leg_ce)
        pe_data = self._data.get_ticker_data(leg_pe)

        if ce_data is None or pe_data is None:
            print("No data found for ", leg_ce, " or ", leg_pe)
            return

        ce_price = ce_data["close"]
        pe_price = pe_data["close"]
        straddle_price = ce_price + pe_price
        print("straddle_price",straddle_price)
        # Set base straddle price for the day
        if self.day_straddle_base is None:
            self.day_straddle_base = straddle_price
            return
        straddle_chng=((straddle_price - self.day_straddle_base)/self.day_straddle_base)*100
        print("straddle_chng%",straddle_chng)
        # Entry Condition
        if not self.in_position and straddle_chng > 10:
            print(f"[{self.time}] SHORT STRADDLE TRIGGERED | CE: {ce_price}, PE: {pe_price}, Total: {straddle_price}")
            self.sell(strategy_id="STRADDLE_SPIKE", position_id=self.position_id, leg_id="short_ce", ticker=leg_ce, quantity=1, stop_loss=0, take_profit=0, tag="Day Start")
            self.sell(strategy_id="STRADDLE_SPIKE", position_id=self.position_id, leg_id="short_pe", ticker=leg_pe, quantity=1, stop_loss=0, take_profit=0, tag="Day Start")
            self.in_position = True

        # Exit Condition
        elif self.in_position and straddle_chng <= 0:
            print(f"[{self.time}] EXITING STRADDLE | CE: {ce_price}, PE: {pe_price}, Total: {straddle_price}")
            for trade in self.active_trades:
                print("trade",trade)
                trade.close(trade.size, tag="Day End")
            self.in_position = False
        
        if current_time >= time(15,15) and current_time <= time(15,30):
            for trade in self.active_trades:
                print("trade",trade)
                trade.close(trade.size, tag="Day End")
                print("trade closed day end: ",trade.size)
            self.in_position = False
        
    
        self.day_straddle_base=straddle_price


In [17]:
# db_path = "nifty_1min_desiquant.duckdb"
db_path = "nifty_opt_icici_1min.duckdb"

bt = Backtest(db_path=db_path, strategy=StraddleSpikeShort, cash=10000000, commission_per_contract=0.65, option_multiplier=75)
stats = bt.run(start_date="2023-01-01", end_date="2024-01-30")
print(stats)

Identifying tables in date range...
Found 220 tables out of 966 total tables with data in range


Backtesting Options Strategy:   0%|          | 0/220 [00:00<?, ?it/s]

straddle_price 333.85
straddle_price 334.8
straddle_chng% 0.28455344
straddle_price 334.45
straddle_chng% -0.10453274
straddle_price 329.75
straddle_chng% -1.405296
straddle_price 333.8
straddle_chng% 1.2281995
straddle_price 335.1
straddle_chng% 0.38946027
straddle_price 335.45
straddle_chng% 0.10444826
straddle_price 334.84998
straddle_chng% -0.17887512
straddle_price 335.2
straddle_chng% 0.104535356
straddle_price 332.2
straddle_chng% -0.89498806
straddle_price 331.0
straddle_chng% -0.36123183
straddle_price 335.2
straddle_chng% 1.2688859
straddle_price 334.35
straddle_chng% -0.25358176
straddle_price 332.5
straddle_chng% -0.5533142
straddle_price 334.6
straddle_chng% 0.63158077
straddle_price 334.45
straddle_chng% -0.044827823
straddle_price 336.45
straddle_chng% 0.5979967
straddle_price 334.55
straddle_chng% -0.56472707
straddle_price 333.4
straddle_chng% -0.34374353
straddle_price 334.1
straddle_chng% 0.20996167
straddle_price 335.09998
straddle_chng% 0.29930243
straddle_price 32

Backtesting Options Strategy:   1%|          | 2/220 [00:00<00:14, 14.69it/s]

straddle_price 414.7
straddle_chng% 0.97394687
straddle_price 412.35
straddle_chng% -0.56667614
straddle_price 403.7
straddle_chng% -2.097731
straddle_price 407.0
straddle_chng% 0.8174356
straddle_price 406.15
straddle_chng% -0.20884672
straddle_price 406.5
straddle_chng% 0.08617657
straddle_price 407.0
straddle_chng% 0.123001225
straddle_price 409.2
straddle_chng% 0.54054356
straddle_price 407.35
straddle_chng% -0.45210314
straddle_price 407.35
straddle_chng% 0.0
straddle_price 411.7
straddle_chng% 1.0678792
straddle_price 414.4
straddle_chng% 0.65581286
straddle_price 408.0
straddle_chng% -1.5444001
straddle_price 409.3
straddle_chng% 0.31862444
straddle_price 409.65
straddle_chng% 0.085513346
straddle_price 409.65
straddle_chng% 0.0
straddle_price 412.65002
straddle_chng% 0.7323399
straddle_price 409.45
straddle_chng% -0.7754785
straddle_price 409.5
straddle_chng% 0.012208521
straddle_price 409.55
straddle_chng% 0.012207031
straddle_price 411.45
straddle_chng% 0.46392977
straddle_pr

...

Backtesting Options Strategy:  96%|█████████▋| 212/220 [00:13<00:00, 15.46it/s]

straddle_price 258.05
straddle_price 258.75
straddle_chng% 0.27127
straddle_price 257.7
straddle_chng% -0.4057924
straddle_price 248.65
straddle_chng% -3.5118423
straddle_price 249.9
straddle_chng% 0.50271463
straddle_price 250.54999
straddle_chng% 0.26010162
straddle_price 250.4
straddle_chng% -0.05986586
straddle_price 251.85
straddle_chng% 0.5790784
straddle_price 252.85
straddle_chng% 0.39706174
straddle_price 250.4
straddle_chng% -0.96895874
straddle_price 251.95
straddle_chng% 0.6190108
straddle_price 251.25
straddle_chng% -0.27783167
straddle_price 249.35
straddle_chng% -0.75621647
straddle_price 249.70001
straddle_chng% 0.14036739
straddle_price 249.0
straddle_chng% -0.28034127
straddle_price 250.59999
straddle_chng% 0.6425666
straddle_price 249.25
straddle_chng% -0.5387035
straddle_price 247.95001
straddle_chng% -0.5215598
straddle_price 248.0
straddle_chng% 0.020160431
straddle_price 249.04999
straddle_chng% 0.42338216
straddle_price 248.65
straddle_chng% -0.16060787
straddle

Backtesting Options Strategy:  98%|█████████▊| 216/220 [00:13<00:00, 16.12it/s]

straddle_price 243.75
straddle_price 245.54999
straddle_chng% 0.73845655
straddle_price 243.95
straddle_chng% -0.65159476
straddle_price 243.65
straddle_chng% -0.12297727
straddle_price 243.5
straddle_chng% -0.061561212
straddle_price 240.75
straddle_chng% -1.1293635
straddle_price 240.75
straddle_chng% 0.0
straddle_price 240.85
straddle_chng% 0.0415394
straddle_price 241.65
straddle_chng% 0.33215186
straddle_price 242.04999
straddle_chng% 0.16552614
straddle_price 242.65001
straddle_chng% 0.2478915
straddle_price 241.65
straddle_chng% -0.4121225
straddle_price 241.20001
straddle_chng% -0.18621217
straddle_price 241.15
straddle_chng% -0.020737275
straddle_price 241.90001
straddle_chng% 0.31101608
straddle_price 241.35
straddle_chng% -0.22736792
straddle_price 240.9
straddle_chng% -0.18645626
straddle_price 239.65001
straddle_chng% -0.5188812
straddle_price 239.15
straddle_chng% -0.20864396
straddle_price 239.95001
straddle_chng% 0.33452576
straddle_price 239.1
straddle_chng% -0.354243


straddle_price 282.1
straddle_price 281.40002
straddle_chng% -0.24813247
straddle_price 277.85
straddle_chng% -1.2615558
straddle_price 279.1
straddle_chng% 0.449883
straddle_price 279.55
straddle_chng% 0.16122596
straddle_price 276.25
straddle_chng% -1.1804643
straddle_price 283.4
straddle_chng% 2.5882332
straddle_price 280.25
straddle_chng% -1.1115011
straddle_price 281.2
straddle_chng% 0.3389874
straddle_price 281.9
straddle_chng% 0.24892662
straddle_price 283.95
straddle_chng% 0.72721475
straddle_price 282.15002
straddle_chng% -0.6339101
straddle_price 271.9
straddle_chng% -3.6328301
straddle_price 271.8
straddle_chng% -0.036780473
straddle_price 272.65
straddle_chng% 0.31273222
straddle_price 271.7
straddle_chng% -0.34842536
straddle_price 279.65
straddle_chng% 2.9260147
straddle_price 279.65
straddle_chng% 0.0
straddle_price 279.55
straddle_chng% -0.03576117
straddle_price 278.5
straddle_chng% -0.3755993
straddle_price 279.05
straddle_chng% 0.19748215
straddle_price 279.45
stradd

In [9]:
from core.wfo import WalkForwardOptimizer

constraint = lambda x: x['upper_threshold'] > x['lower_threshold']


wfo = WalkForwardOptimizer(
    strategy=IV_Slope,
    optimization_params={
        # 'upper_threshold': [-0.15 ,-0.1, 0.1, 0.15, 0.2, 0.25, 0.3],
        # 'lower_threshold': [-0.15 ,-0.1 ,0, 0.05, 0.1, 0.15, 0.2]
        'upper_threshold': [0.1, 0.15, 0.2, 0.25],
        'lower_threshold': [ 0.1, 0.15, 0.2]
    },
    # constraint=constraint,
    maximize='Sharpe Ratio',
)

In [ ]:
# def optimize_stock(self, stock, timeframe, db_path, exchange = None, training_candles = 2000, testing_candles = 200):
    
wfo.optimize_stock(
    stock='NIFTY',
    timeframe='1min',
    db_path='../core/nifty_1min_desiquant.duckdb',
    exchange='NSE',
    training_candles=6000,
    testing_candles=3000,
    start_date='2022-01-01',
    end_date='2022-12-31',
    # method='sambo',
    # max_tries=10
)

In [ ]:
bt.tear_sheet()